In [1]:
import re
import os
from tqdm import tqdm
from pathlib import Path
import numpy as np
import pandas as pd
from time import process_time
import io
import tensorflow as tf
import codecs
from sklearn.model_selection import train_test_split
from numpy import array
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from keras.utils.vis_utils import plot_model
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Flatten
from tensorflow.keras.layers import Dropout
from tensorflow.keras.layers import Embedding
from tensorflow.keras.layers import Conv1D
from tensorflow.keras.layers import MaxPooling1D
from tensorflow.keras.layers import concatenate
# !apt install unzip

In [ ]:
from nltk import ne_chunk
import nltk
# nltk.download('all')


# Pre-Processing

In [ ]:
# data = !unzip /content/documents.zip -d /content/drive/MyDrive/TextClassificationAssignment
# !unzip /content/documents.zip

In [ ]:
data=os.listdir('/content/documents')
print("Lenght of data = ",len(data))
print("Type of data",type(data))

Lenght of data =  18828
Type of data <class 'list'>


In [ ]:
def process_emails(content):
    em = [] # for each doc
    st = ""  # for each doc
#     emails=[]
    # email=re.findall(r"\b[a-zA-Z0-9.\-+_]+@[A-Za-z0-9.\-+_]+", content,flags=re.MULTILINE)
    email=re.findall(r'[\w\-\.]+@[\w\.-]+\b', content,flags=re.MULTILINE)
    for i in email:
      temp=[]
      temp = i.split('@')[1]      #taking text after @
      temp = temp.split('.')     #a list containing words split by "."
      temp=[i for i in temp if i not in('com','COM')]    
      for i in temp:           #removing words less than 3
          if len(i)>2:
              em.append(i)
    for i in set(em):            #joining all the words in a string
        st+=i
        st+=' '
    
#     emails.append(st.replace("-"," ").lower())
    for i in email:
        content=re.sub(i,' ',content)    #removing the email
    return content , st

def pp_subject(doc):
        sub = re.findall('Subject:(.*)\n',doc)[0].split(':')[-1]
        sub = re.sub(r"[^a-zA-Z0-9]+"," ",sub)  # rule 3
        sub= re.sub('[A-Z]+', lambda m: m.group(0).lower(), sub)
        doc = re.sub("Subject:(.*)\n",' ',doc)  # rule 4 
        return doc , sub

def decontracted(phrase):
    # specific
    phrase = re.sub(r"won't", "will not", phrase)
    phrase = re.sub(r"can\'t", "can not", phrase)

    # general
    phrase = re.sub(r"n\'t", " not", phrase)
    phrase = re.sub(r"\'re", " are", phrase)
    phrase = re.sub(r"\'s", " is", phrase)
    phrase = re.sub(r"\'d", " would", phrase)
    phrase = re.sub(r"\'ll", " will", phrase)
    phrase = re.sub(r"\'t", " not", phrase)
    phrase = re.sub(r"\'ve", " have", phrase)
    phrase = re.sub(r"\'m", " am", phrase)
    return phrase

def lower_large_words(text):
    text=text.lower()
    text_list=text.split()
    text_list=[element for element in text_list if len(element)>2]
    text_list=[element for element in text_list if len(element)<15]
#     for element in text_list:
#         if(len(element)>15):
#             text_list.remove(element)
#         if(len(element)<3):
#             text_list.remove(element)
    updated_text=' '.join(text_list)
    updated_text = re.sub(r'[^a-z_ ]', '', updated_text)
    return updated_text
def preprocessing(doc):
    processed_emails=[]
    processed_subjects=[]
    #text has to be sent after removing subject and emails
#     start=process_time()
    content , processed_emails_string=process_emails(doc)
    processed_emails.append(processed_emails_string)
    content , processed_subject = pp_subject(content)
    processed_subjects.append(processed_subject)
    unwanted = "[!@#$;:!*%)><(&^~\/]"
    sub1 = re.sub('(From:.*)\n',' ',content) # Removing sentences that start with From:
    sub2 = re.sub('(Write to:.*)\n',' ',sub1) #Removing sentences that start with Write to:
    sub3 = re.sub("[\(\<].*?[\)\>]", "", sub2)   #Removing words in between <Anyword> and (Anywords)
    sub4 = re.sub(r'\s+',' ',sub3) #Removing tabs, \n, white spaces
    sub5 = re.sub(r'\w+:\s?','',sub4) #Removing words that end with :
    sub6 = decontracted(sub5)
    sub7 = re.sub(unwanted,'',sub6) #Removing unwanted special characters
    sub8 = chunking(sub7)  # performing chunking
    sub9 = re.sub(r'[0-9]', '', sub8) #Remove digits from the text
    sub10= _removal(sub9) #Removing Underscore before and after any word
    processed_text =lower_large_words(sub10)# Removing all characters except lower case alphabets, spaces and _.
#     print('Time taken to process each file =',start-process_time())
    return processed_emails, processed_subjects, processed_text

def chunking(text):
#     chunked = ne_chunk(doc)
#     return [ " ".join(w for w, t in elt) for elt in chunked if isinstance(elt, nltk.Tree) ]
    word = nltk.word_tokenize(text)   
    pos_tag = nltk.pos_tag(word)   
    chunk = nltk.ne_chunk(pos_tag)   
    NE = [ " ".join(w for w, t in ele) for ele in chunk if isinstance(ele, nltk.Tree)]   
    # print (NE)
    # print(type(NE))
    set={*NE}
    list=[*set]
    list=[name for name in list if ' ' in name]
    # updated_list=[name.replace(' ','_') for name in list]
    updated_text=text
    for word in list:
        updated_text=updated_text.replace(word,word.replace(' ','_'))
    return updated_text

def _removal(text):
    # start=process_time()
    _char=[word for word in text.split() if '_' in word]
    for element in _char:
        if element.startswith('_')|element.endswith('_'):
            updated_word=element.replace('_','')
            text=text.replace(element,updated_word)
        temp=element.split('_')
        if(len(element)!=0):
            for ele in temp:
                if(len(ele)<3):
                    temp.remove(ele)
            temp_string='_'.join(temp)
            text=text.replace(element,temp_string)
    # print(process_time()-start)
    return text

In [ ]:
# https://towardsdatascience.com/how-i-preprocessed-text-data-using-regular-expressions-for-my-text-classification-task-cnn-cb206e7274ed
def label_doc_name(file):
  label=[]
  doc_num=[]
  # for filename in os.listdir('/content/drive/MyDrive/TextClassificationAssignment/documents'):
  i,j = filename.split('_')
  j = int(j.split('.')[0])
  label.append(i) 
  doc_num.append(j)


#https://www.geeksforgeeks.org/how-to-read-multiple-text-files-from-folder-in-python/
def read_text_file(file_path):
    # with open(file_path,'rb') as f:
    with codecs.open(file_path,'rU',encoding='latin1') as f:
        text=f.read()
        text=str(text)
        return text
start=process_time()
label=[]
doc_num=[]
processed_emails=[]
processed_subjects=[]
processed_texts=[]
 # for each doc
# iterate through all file
for file in tqdm(data):
    i,j = file.split('_')
    j = int(j.split('.')[0])
    label.append(i) 
    doc_num.append(j)
    path = "/content/documents/"
    file_path = f"{path}{file}"
    # call read text file function
    content=read_text_file(file_path)
    print(file_path)
    processed_email, processed_subject, processed_text = preprocessing(content)
    processed_emails.append(processed_email)
    processed_subjects.append(processed_subject)
    processed_texts.append(processed_text)
print('Time taken to process this f= ',start-process_time())
    








  0%|          | 0/18828 [00:00<?, ?it/s]






  0%|          | 2/18828 [00:00<15:42, 19.97it/s]

/content/documents/sci.crypt_15342.txt
/content/documents/comp.windows.x_66914.txt
/content/documents/comp.graphics_38468.txt
/content/documents/sci.space_61348.txt
/content/documents/alt.atheism_53402.txt









  0%|          | 5/18828 [00:00<16:16, 19.27it/s]






  0%|          | 8/18828 [00:00<14:57, 20.96it/s]

/content/documents/misc.forsale_74754.txt
/content/documents/talk.politics.mideast_76212.txt
/content/documents/rec.autos_103226.txt
/content/documents/talk.politics.misc_176865.txt









  0%|          | 10/18828 [00:00<24:16, 12.92it/s]

...

/content/documents/rec.sport.hockey_52576.txt
/content/documents/talk.politics.guns_54236.txt
/content/documents/misc.forsale_76449.txt
/content/documents/misc.forsale_76754.txt
/content/documents/comp.os.ms-windows.misc_9614.txt
/content/documents/sci.electronics_53554.txt









100%|█████████▉| 18825/18828 [1:00:37<00:00,  5.98it/s]








/content/documents/rec.autos_102790.txt
/content/documents/comp.sys.ibm.pc.hardware_60188.txt


100%|██████████| 18828/18828 [1:00:37<00:00,  5.18it/s]

/content/documents/comp.windows.x_67561.txt
Time taken to process this f=  -3293.9232108670003


In [ ]:
df1 = pd.DataFrame(list(zip(label, doc_num, processed_emails, processed_subjects, processed_texts)),
               columns =['label', 'doc_Num', 'processed_emails', 'processed_subjects', 'processed_texts'])
# df1.to_csv('/content/drive/MyDrive/TextClassificationAssignment/pre_processed_data.csv',index=False)
df1.to_hdf('/content/drive/MyDrive/TextClassificationAssignment/pre_processed_data.h5', key='df', mode='w')

/usr/local/lib/python3.7/dist-packages/pandas/core/generic.py:2449: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed,key->block1_values] [items->Index(['label', 'processed_emails', 'processed_subjects', 'processed_texts'], dtype='object')]

  encoding=encoding,


In [2]:
data=pd.read_csv('/content/drive/MyDrive/TextClassificationAssignment/pre_processed_data.csv')
data.head()
# df.shape

label  ...                                    processed_texts
0       sci.crypt  ...  article note that measures protect yourself fr...
1  comp.windows.x  ...  article have got problem concerning the maximu...
2   comp.graphics  ...  help how you write the second bankpage memory ...
3       sci.space  ...  article just few contributions from the space ...
4     alt.atheism  ...  article the line about atheists haveing someth...

[5 rows x 5 columns]

For checking of code with alt.atheism_49960

In [ ]:
# The [] and quotes in the processed_emails and processe_subjects have been stripped down in the next cells
data.loc[data['doc_Num']==49960]

label  ...                                    processed_texts
3603  alt.atheism  ...  last december usa freedom from religion founda...

[1 rows x 5 columns]

Joining text in Processed_emails,Processed_subjects and Processed_texts columns

In [ ]:
# data["combined_texts"] = data["processed_emails"] + " " + data["processed_subjects"]+ " " +data["processed_texts"]
# data.drop(['combined_texts'], axis='columns', inplace=True)
data.head()


label  ...                                    processed_texts
0       sci.crypt  ...  article note that measures protect yourself fr...
1  comp.windows.x  ...  article have got problem concerning the maximu...
2   comp.graphics  ...  help how you write the second bankpage memory ...
3       sci.space  ...  article just few contributions from the space ...
4     alt.atheism  ...  article the line about atheists haveing someth...

[5 rows x 5 columns]

In [3]:
# Ref: https://stackoverflow.com/questions/38147447/how-to-remove-square-bracket-from-pandas-dataframe
##  Removing [] and '' from the text in processed_emails and processed_subjects
data['processed_subjects'] = data['processed_subjects'].str.strip("['']").astype(str)
data['processed_emails'] = data['processed_emails'].str.strip("['']").astype(str)
data.head()

label  ...                                    processed_texts
0       sci.crypt  ...  article note that measures protect yourself fr...
1  comp.windows.x  ...  article have got problem concerning the maximu...
2   comp.graphics  ...  help how you write the second bankpage memory ...
3       sci.space  ...  article just few contributions from the space ...
4     alt.atheism  ...  article the line about atheists haveing someth...

[5 rows x 5 columns]

In [4]:
# data=data.drop(columns='combined_texts', axis=1)
data["combined_texts"] = data["processed_emails"].fillna('') + " " + data["processed_subjects"].fillna('')+ " " +data["processed_texts"].fillna('')
data.head()

label  ...                                     combined_texts
0       sci.crypt  ...  EDU ColoState yuma netcom ACNS   once tapped y...
1  comp.windows.x  ...  irzr17 TU-Dresden igd Inf fhg inf IRS tu-dresd...
2   comp.graphics  ...  massey   page flipping in vga 320x200x256 mode...
3       sci.space  ...  weizmann siss81 rpslmc pashosh edu wisdom   lo...
4     alt.atheism  ...  mcl ucsb wisc edu whipple snake2   amusing ath...

[5 rows x 6 columns]

In [ ]:
data['combined_texts'] = data['combined_texts'].str.lower()

In [ ]:
docs=list(data['combined_texts'])
print(len(docs))

18828


# Train-Test Split for Classification

In [5]:
Y=data['label']   # .values may be somewhere
# Y.head()
X=data['combined_texts'].str.lower()
print('Shape of X: ',X.shape)
print('Shape of Y: ',Y.shape)

Shape of X:  (18828,)
Shape of Y:  (18828,)


In [6]:
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.25, random_state=1, stratify=Y)

In [ ]:
print(y_train.head())

8158           rec.sport.baseball
15831                   rec.autos
2709      comp.os.ms-windows.misc
7033     comp.sys.ibm.pc.hardware
14149              comp.windows.x
Name: label, dtype: object


In [7]:
from sklearn.preprocessing import LabelEncoder
label_encoder = LabelEncoder()
y_train = label_encoder.fit_transform(y_train)
y_test = label_encoder.fit_transform(y_test)
y_train = tf.keras.utils.to_categorical(y_train, num_classes=20)
y_test  = tf.keras.utils.to_categorical(y_test, num_classes=20)

In [26]:
print(y_train[0:5])

[[0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]]


In [ ]:
len(y_train)

14121

## Tokenization

In [ ]:
# from nltk.tokenize import word_tokenize 
# from keras.preprocessing.sequence import pad_sequences
# from keras.models import Sequential
# from keras.layers import Dense
# from keras.layers import Flatten
# from keras.preprocessing.text import Tokenizer
# from keras.layers.embeddings import Embedding

In [9]:
#Ref: https://stackoverflow.com/questions/49073673/include-punctuation-in-keras-tokenizer
#Ref: https://machinelearningmastery.com/use-word-embedding-layers-deep-learning-keras/
t = Tokenizer(num_words=1000, filters='!"#$%&()*+,-/:;<=>?@[\\]^_`{|}~\t\n')
t.fit_on_texts(X_train)
vocab_size = len(t.word_index) + 1
# integer encode the documents
# encoded_docs = t.texts_to_sequences(docs)
encoded_docs_X_train = t.texts_to_sequences(X_train)
encoded_docs_X_test = t.texts_to_sequences(X_test)
# encoded_docs_y_train = t.texts_to_sequences(y_train)
# encoded_docs_y_test = t.texts_to_sequences(y_test)
print(encoded_docs_X_train)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [10]:
length_words=[len(x.split()) for x in X_train]
print('max lenght document= ',max(length_words))
print('min length document= ',min(length_words))
print('mean length document=', sum(length_words)/len(length_words))
# Since the maximum lenghtiest document contains 9026 words we will be pad all words to 9026

max lenght document=  9026
min length document=  3
mean length document= 185.63040861128815


In [11]:
vocab_size=len(t.word_index)+1
print(vocab_size)

91492


In [ ]:
print(type(y_train[0][0]))

<class 'numpy.float32'>


In [12]:
max_length = 1000
X_train = pad_sequences(encoded_docs_X_train, maxlen=max_length, padding='post')
X_test = pad_sequences(encoded_docs_X_test, maxlen=max_length, padding='post')
# y_train = pad_sequences(y_train, maxlen=max_length, padding='post') 
# y_test = pad_sequences(y_test, maxlen=max_length, padding='post') 
# # print(padded_docs)

Word Embedding with GloVe Vector

In [13]:
#https://stackabuse.com/python-for-nlp-word-embeddings-for-deep-learning-in-keras/
from numpy import array
from numpy import asarray
from numpy import zeros

embeddings_dictionary = dict()
glove_file = open('/content/drive/MyDrive/TextClassificationAssignment/glove.6B.300d.txt','rb' )#,encoding="latin1"

In [14]:
for line in glove_file:
    records = line.split()
    word = records[0]
    # print(records[1:])
    vector_dimensions = asarray(records[1:], dtype='float32')
    embeddings_dictionary [word] = vector_dimensions

glove_file.close()

In [15]:
len(embeddings_dictionary)

400000

In [16]:
embedding_matrix = zeros((vocab_size, 300))
for word, index in t.word_index.items():
    embedding_vector = embeddings_dictionary.get(word)
    if embedding_vector is not None:
        embedding_matrix[index] = embedding_vector

In [17]:
embedding_matrix.shape

(91492, 300)

In [ ]:
# model = Sequential()
# embedding_layer = Embedding(vocab_length, 300, weights=[embedding_matrix], input_length=max_length, trainable=False)
# model.add(embedding_layer)
# model.add(Flatten())
# model.add(Dense(1, activation='sigmoid'))

# Defining Callbacks

In [23]:
# https://medium.com/@thongonary/how-to-compute-f1-score-for-each-epoch-in-keras-a1acd17715a2
from tensorflow.keras.callbacks import Callback
from sklearn.metrics import confusion_matrix, f1_score, precision_score, recall_score, roc_curve, roc_auc_score
class Metrics(Callback):
  def __init__(self,validation_data):
    self.validation_data=validation_data
  def on_train_begin(self, logs={}):
    self.val_f1s = []
    self.val_recalls = []
    self.val_precisions = []
    # self.val_auc=[]
 
  def on_epoch_end(self, validation_data, epoch, logs={}):
    # print('len of validation data',len(self.validation_data))
    val_predict = np.asarray(self.model.predict(self.validation_data[0]))
    # val_predict_proba=np.asarray(self.model.predict_on_batch(self.validation_data[0]))
    val_targ = self.validation_data[1]
    _val_f1 = f1_score(val_targ, val_predict.round(), average='micro')
    # _val_auc=roc_auc_score(val_targ,val_predict_proba)
    self.val_f1s.append(_val_f1)
    # self.val_auc.append(_val_auc)
    print('_val_f1:{0}'.format(_val_f1))
    # return
  
metrics = Metrics(validation_data=(X_test,y_test))

In [19]:
from tensorflow.keras.callbacks import LearningRateScheduler
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.layers import Dense,Input,Activation
from tensorflow.keras.models import Model
from tensorflow.keras.callbacks import ModelCheckpoint
from keras.callbacks import ReduceLROnPlateau
import random as rn
import tensorflow as tf
import datetime

def changeLearningRate(epoch,learning_rate):
    if(epoch%3==0 & epoch!=0):
      initial_learningrate=0.05
      changed = initial_learningrate*((1-0.05)**epoch)
      print('changed',changed)
      return changed
    else:
      return learning_rate

      # return initial_learningrate*(1-0.05)**epoch

class TerminateNaN(tf.keras.callbacks.Callback):
        
    def on_epoch_end(self, epoch, logs={}):
        loss = logs.get('loss')
        if loss is not None:
            if np.isnan(loss) or np.isinf(loss):
                print("Invalid loss and terminated at epoch {}".format(epoch))
                self.model.stop_training = True

terminateNan =  TerminateNaN()              

In [20]:
%load_ext tensorboard
# !rm -rf "/content/logs\fit\20210523-034400"

In [21]:
#Ref: https://machinelearningmastery.com/develop-n-gram-multichannel-convolutional-neural-network-sentiment-analysis/
# def define_model(length, vocab_size):
	# channel 1
tf.keras.backend.clear_session()
inputs1 = Input(shape=(max_length,))
embedding1 = Embedding(vocab_size, 300, weights=[embedding_matrix], input_length=max_length, trainable=False)(inputs1)
conv1 = Conv1D(filters=2, kernel_size=4, activation='relu')(embedding1)
conv2 = Conv1D(filters=4, kernel_size=4, activation='relu')(embedding1)
conv3 = Conv1D(filters=6, kernel_size=4, activation='relu')(embedding1)
merged1 = concatenate([conv1, conv2, conv3])
pool1 = MaxPooling1D(pool_size=2)(merged1)
conv4 = Conv1D(filters=3, kernel_size=4, activation='relu')(pool1)
conv5 = Conv1D(filters=5, kernel_size=4, activation='relu')(pool1)
conv6 = Conv1D(filters=7, kernel_size=4, activation='relu')(pool1)
merged2 = concatenate([conv4, conv5, conv6])
pool2 = MaxPooling1D(pool_size=2)(merged2)
conv7 = Conv1D(filters=8, kernel_size=8, activation='relu')(pool1)
flat1 = Flatten()(conv7)
drop1 = Dropout(0.5)(flat1)
dense1 = Dense(3, activation='relu')(drop1)
outputs = Dense(20, activation='softmax')(dense1)
log_dir="logs\\fit\\" + datetime.datetime.now().strftime("%Y%m%d-%H%M%S")
tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=log_dir,histogram_freq=1, write_graph=True,write_grads=True)
rlrop=ReduceLROnPlateau(monitor='val_loss',factor=0.9,patience=1)
lrschedule = LearningRateScheduler(changeLearningRate, verbose=1)
optimizer = tf.keras.optimizers.SGD(learning_rate=0.01, momentum=0.9)
earlystop = EarlyStopping(monitor='val_loss', patience=2, verbose=1)#, min_delta=0.03
filepath="/content/drive/MyDrive/TextClassificationAssignment/model_save/best_model_1-{epoch:02d}-{val_loss:.4f}.hdf5"
checkpoint = ModelCheckpoint(filepath=filepath, monitor='val_loss', save_best_only=True,  verbose=1, mode='auto') #
callback_list = [Metrics(validation_data=(X_test,y_test)), lrschedule, earlystop, checkpoint,rlrop, terminateNan, tensorboard_callback]


model = Model(inputs=inputs1, outputs=outputs)
	# compile
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
	# summarize
print(model.summary())
plot_model(model, show_shapes=True, to_file='multichannel.png')
model.fit(X_train,y_train,epochs=10, validation_data=(X_test,y_test), batch_size=10, callbacks=callback_list)
# return model
	# flat1 = Flatten()(pool1)
	# channel 2
	# inputs2 = Input(shape=(length,))
	# embedding2 = Embedding(vocab_size, 100)(inputs2)
	
	# drop2 = Dropout(0.5)(conv2)
	# pool2 = MaxPooling1D(pool_size=2)(drop2)
	# flat2 = Flatten()(pool2)
	# channel 3
	# inputs3 = Input(shape=(length,))
	# embedding3 = Embedding(vocab_size, 100)(inputs3)
	
	# drop3 = Dropout(0.5)(conv3)
	# pool3 = MaxPooling1D(pool_size=2)(drop3)
	# flat3 = Flatten()(pool3)
	# # merge
	
	# # interpretation
	# dense1 = Dense(10, activation='relu')(merged)
	# outputs = Dense(1, activation='sigmoid')(dense1)
	

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, 1000)]       0                                            
__________________________________________________________________________________________________
embedding (Embedding)           (None, 1000, 300)    27447600    input_1[0][0]                    
__________________________________________________________________________________________________
conv1d (Conv1D)                 (None, 997, 2)       2402        embedding[0][0]                  
__________________________________________________________________________________________________
conv1d_1 (Conv1D)               (None, 997, 4)       4804        embedding[0][0]                  
______________________________________________________________________________________________

In [24]:
tf.keras.backend.clear_session()

In [27]:
inputs1 = Input(shape=(max_length,))
embedding1 = Embedding(vocab_size, 300, weights=[embedding_matrix], input_length=max_length, trainable=False)(inputs1)
conv1 = Conv1D(filters=2, kernel_size=4, activation='relu')(embedding1)
conv2 = Conv1D(filters=4, kernel_size=4, activation='relu')(embedding1)
conv3 = Conv1D(filters=6, kernel_size=4, activation='relu')(embedding1)
merged1 = concatenate([conv1, conv2, conv3])
pool1 = MaxPooling1D(pool_size=2)(merged1)
conv4 = Conv1D(filters=3, kernel_size=4, activation='relu')(pool1)
conv5 = Conv1D(filters=5, kernel_size=4, activation='relu')(pool1)
conv6 = Conv1D(filters=7, kernel_size=4, activation='relu')(pool1)
merged2 = concatenate([conv4, conv5, conv6])
pool2 = MaxPooling1D(pool_size=2)(merged2)
conv7 = Conv1D(filters=8, kernel_size=8, activation='relu')(pool1)
flat1 = Flatten()(conv7)
drop1 = Dropout(0.5)(flat1)
dense1 = Dense(10, activation='relu')(drop1)
drop2 = Dropout(0.5)(dense1)
dense2 = Dense(10, activation='relu')(drop2)
outputs = Dense(20, activation='softmax')(dense2)
log_dir="logs\\fit\\" + datetime.datetime.now().strftime("%Y%m%d-%H%M%S")
tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=log_dir,histogram_freq=1, write_graph=True,write_grads=True)
rlrop=ReduceLROnPlateau(monitor='val_loss',factor=0.9,patience=1)
lrschedule = LearningRateScheduler(changeLearningRate, verbose=1)
optimizer = tf.keras.optimizers.SGD(learning_rate=0.01, momentum=0.9)
earlystop = EarlyStopping(monitor='val_loss', patience=2, verbose=1)#, min_delta=0.03
filepath="/content/drive/MyDrive/TextClassificationAssignment/model_save/best_model_1-{epoch:02d}-{val_loss:.4f}.hdf5"
checkpoint = ModelCheckpoint(filepath=filepath, monitor='val_loss', save_best_only=True,  verbose=1, mode='auto') #
callback_list = [Metrics(validation_data=(X_test,y_test)), lrschedule, earlystop, checkpoint,rlrop, terminateNan, tensorboard_callback]


model = Model(inputs=inputs1, outputs=outputs)
	# compile
model.compile(loss='categorical_crossentropy', optimizer=optimizer, metrics=['accuracy'])
	# summarize
print(model.summary())
plot_model(model, show_shapes=True, to_file='multichannel.png')
model.fit(X_train,y_train,epochs=10, validation_data=(X_test,y_test), batch_size=10, callbacks=callback_list)

Model: "model_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            [(None, 1000)]       0                                            
__________________________________________________________________________________________________
embedding_1 (Embedding)         (None, 1000, 300)    27447600    input_2[0][0]                    
__________________________________________________________________________________________________
conv1d_7 (Conv1D)               (None, 997, 2)       2402        embedding_1[0][0]                
__________________________________________________________________________________________________
conv1d_8 (Conv1D)               (None, 997, 4)       4804        embedding_1[0][0]                
____________________________________________________________________________________________